# Dataset class

In [1]:
!pip install -q -U accelerate=='0.25.0' peft=='0.7.1' bitsandbytes=='0.41.3.post2' transformers=='4.36.1' trl=='0.7.4'

In [2]:
import os
import requests
from datasets import load_dataset
import torch
from PIL import Image
from torch.utils.data import DataLoader
from tqdm import tqdm
import pickle
from torchvision.transforms import v2
from torch.utils.data import RandomSampler, DataLoader, Subset
import pytesseract
import pandas as pd
from torchvision.io import read_image
from torch.utils.data import Dataset
from torchvision import datasets
from torchvision.transforms import ToTensor
import matplotlib.pyplot as plt
import json as js
import numpy as np
from urllib.parse import urlparse
import csv
import torchvision
import re
import bitsandbytes as bnb
import torch.nn as nn
import transformers
from datasets import Dataset
from peft import LoraConfig, PeftConfig
from trl import SFTTrainer
from transformers import (AutoModelForCausalLM, 
                          AutoTokenizer, 
                          BitsAndBytesConfig, 
                          TrainingArguments, 
                          pipeline, 
                          logging)
from sklearn.metrics import (accuracy_score, 
                             classification_report, 
                             confusion_matrix)
from sklearn.model_selection import train_test_split
from transformers import AutoModelForCausalLM, AutoTokenizer
from tqdm.auto import tqdm, trange
import torch
import torch.nn as nn
import torch.nn.functional as F
#import peft

import transformers
from datasets import load_dataset

import random

2024-04-13 04:06:13.590000: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-04-13 04:06:13.590098: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-04-13 04:06:13.726570: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
/opt/conda/lib/python3.10/site-packages/trl/trainer/ppo_config.py:141: UserWarning: The `optimize_cuda_cache` arguement will be deprecated soon, please use `optimize_device_cache` instead.
  warnings.warn(


In [3]:
# !pip install pytesseract -q

In [4]:
class VQA_Dataset(Dataset):
    def __init__(self, annotations_file, img_dir, processor, transform=None, train=True, device='cuda:0'):
        self.img_dir = img_dir
        self.annotations_file = annotations_file
        self.transform = transform
        self.items = []
        self.device = device
        self.processor= processor
        self.img_dir = img_dir
        self.train = train
        if train:
            with open(self.annotations_file) as file:
                for line in file:
                    json = js.loads(line)

                    evidence_pages = np.array(json['evidence_pages']) - 1 #индексы с единицы а надо с нуля
                    image_urls = np.array(json['image_urls'])
                    #image_urls = np.take(image_urls, evidence_pages)
                    deck_name = json['deck_name']

                    image_paths = os.listdir(os.path.join(img_dir, deck_name))
                    
                    if len(image_paths) == 20:
                        self.items.append({
                        'deck_name':json['deck_name'],
                        'answer':json['answer'],
                        'question':json['question'],
                        'image_paths':image_paths
                    })
                    else:
                        if not self.train:
                            self.items.append({
                        'deck_name':json['deck_name'],
                        'answer':json['answer'],
                        'question':json['question'],
                        'image_paths': [image_paths[0]] * 20
                    })
                        
        else:
                with open(self.annotations_file, 'r') as file:
                    csv_reader = csv.DictReader(file)
                    for row in csv_reader:
                        deck_name = row['deck_name']
                        
                        image_paths = os.listdir(os.path.join(img_dir, deck_name))

                        self.items.append({
                            'deck_name':row['deck_name'],
                            'question':row['question'],
                            'image_paths':image_paths
                        })

    def __len__(self):
        return len(self.items)

    def __getitem__(self, idx):
        item = self.items[idx]
        images = []
        
        for image_path in item['image_paths']:
            img = Image.open(os.path.join(self.img_dir, item['deck_name'], image_path)).convert("RGB")
            #img = np.array(img)
            #img = self.transform(img)
            text = pytesseract.image_to_string(img)


            text = re.sub(r'[^A-Za-z0-9 ]+', '', text)
            images.append(text)
            
        input_text = f'[INST]You are a helpful question answering assistant. The context and the question to this context are given, answer to the question as short as possible. Dont add any explanation, just the answer, the answer should not exceed 5 words!\n Context:{".".join(images)}\nQuastion:{item["question"]}Answer:[/INST] '
        #encoding = self.processor(images, text=item['question'], padding="max_length", max_length=512, truncation=True, return_tensors="pt")

        #num_images, channals, w, h = encoding['pixel_values'].shape
        #print(encoding['pixel_values'].shape)
        #encoding['pixel_values'] = torch.reshape(encoding['pixel_values'], (num_images*channals, w,h))
        
        if self.train:
            labels = self.processor.tokenizer.encode(
                item['answer'], max_length= 8, pad_to_max_length=True, return_tensors='pt'
            )
            encoding["labels"] = labels
        #else:
            #print(f"{item['question']}")
            
        # remove batch dimension

            
        return input_text

In [5]:
model_name = 'mistralai/Mistral-7B-Instruct-v0.2'

In [6]:
const_seed = 100
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
tokenizer = AutoTokenizer.from_pretrained(model_name, device_map=device)
tokenizer.pad_token_id = tokenizer.eos_token_id

model = AutoModelForCausalLM.from_pretrained(
    model_name, device_map=device, low_cpu_mem_usage=True, offload_state_dict=True,
    load_in_4bit=True, torch_dtype=torch.float32,
)
# for param in model.parameters():
#     param.requires_grad=False

# model.gradient_checkpointing_enable()  # only store a small subset of activations, re-compute the rest.
# model.enable_input_require_grads()     # override an implementation quirk in gradient checkpoints that disables backprop unless inputs require grad
# more on gradient checkpointing: https://pytorch.org/docs/stable/checkpoint.html https://arxiv.org/abs/1604.06174

tokenizer_config.json:   0%|          | 0.00/1.46k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/493k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.80M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/72.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/596 [00:00<?, ?B/s]

...

model-00001-of-00003.safetensors:   0%|          | 0.00/4.94G [00:00<?, ?B/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/4.54G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/111 [00:00<?, ?B/s]

In [7]:
# Инициализируем датасет
annotations_file = '/kaggle/input/qa-over-slides-searching-for-the-information/qa_test.csv'
dir_to_image_folders = '/kaggle/input/qa-over-slides-searching-for-the-information/test/test'
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
batch_size = 1

transform = v2.Compose([
    #v2.Resize((size, size)),
     v2.ToTensor()
])

test_dataset = VQA_Dataset(annotations_file=annotations_file,
                      img_dir=dir_to_image_folders,
                      transform=transform,
                      processor=tokenizer,
                        train=False,
                      device=device)
test_dataset = test_dataset

test_dataloader =  DataLoader(test_dataset, batch_size=batch_size, shuffle=False, pin_memory=True)

/opt/conda/lib/python3.10/site-packages/torchvision/transforms/v2/_deprecated.py:43: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.
  warnings.warn(


In [8]:
next(iter(test_dataloader))

['[INST]You are a helpful question answering assistant. The context and the question to this context are given, answer to the question as short as possible. Dont add any explanation, just the answer, the answer should not exceed 5 words!\n Context:RO smartphone  Data consumption insights.The role of mobile in the digital strategySR ee an ee ae ae nr eesIndustry Value of Mobile SolutionFinance  BankingInsuranceRetailTravel  TransportationHealthcareConstruction  ManufacturingCustomers manage investmentPortofolio and accounts in a mobilecontextCustomers and agents file claims anddocument damages drive claimsresolutionsInteligently target personalised andlocationsensitive marketing offersengage customersProvide customers with updatedinformation specific on their itinerariesand location and enable customerselfserviceProvide patients with improved accessto care safety and quality of carewhile reducing costs and improvingefficiencyEquip employment to managecomplex projects and operations onsi

In [9]:
import pandas as pd
model.eval()
result = []

for idx, batch in zip(tqdm(range(len(test_dataloader)), desc='Validating batch: ...'), test_dataloader):
    encoding = tokenizer(text=batch[0], padding="max_length", max_length=2048, truncation=True, return_tensors="pt")
    encoding = encoding.to(device)
    #with torch.amp.autocast(device_type='cuda', dtype=torch.float16):
    outputs = model.generate(**encoding, max_new_tokens=100, temperature=0.5, do_sample=True)
    input = tokenizer.batch_decode(outputs, skip_special_tokens = True)[0]
    try:
        print(input)
        substr2 = r"[/INST]"
        substr = input[input.index(substr2)+len(substr2)+1:len(input)]
        result.append(substr)
        if substr == '' or substr == " ":
            result.append('No aswer')
        print(substr)
    except:
        result.append('No aswer')
#     if idx != 0 and idx % 10 == 0:
#         print(idx)
#         break

df = pd.DataFrame()
df['ID'] = np.array(list(range(len(result))))
df['pred_answer'] = np.array(result)

Validating batch: ...:   0%|          | 0/1014 [00:00<?, ?it/s]

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]You are a helpful question answering assistant. The context and the question to this context are given, answer to the question as short as possible. Dont add any explanation, just the answer, the answer should not exceed 5 words!
 Context:RO smartphone  Data consumption insights.The role of mobile in the digital strategySR ee an ee ae ae nr eesIndustry Value of Mobile SolutionFinance  BankingInsuranceRetailTravel  TransportationHealthcareConstruction  ManufacturingCustomers manage investmentPortofolio and accounts in a mobilecontextCustomers and agents file claims anddocument damages drive claimsresolutionsInteligently target personalised andlocationsensitive marketing offersengage customersProvide customers with updatedinformation specific on their itinerariesand location and enable customerselfserviceProvide patients with improved accessto care safety and quality of carewhile reducing costs and improvingefficiencyEquip employment to managecomplex projects and operations onsite 

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]You are a helpful question answering assistant. The context and the question to this context are given, answer to the question as short as possible. Dont add any explanation, just the answer, the answer should not exceed 5 words!
 Context:STORY  PHENOMENON There are many aspect of Big Dataresearch but too little resource too se otlittle talent aw P a Same business objective but increase Ke is Peffectiveness on top of current services  C Y x Problem with Legacy Methodologyapproach using QuestionnaireInterviewsSurveys ok with small scaledata  expensive and took longer time forlarge scale data accuracy issues .vi AM   Label yourProfessional Networks Alumni MAITBUnikomAstra GraphiaClose Friend  FamilyDeviant Art  Photograpt Alumni SMA 3 Malang1M TelkomVarious IT Projecteee.INDUSTRY EFFORTSeeezHOofaetsaboutneOU ar PEFMOON tee sss ecotoraa hour ie cha ne Pen iyo i ae  9aOalCINTA  SalingSilang Twitter Trending Topic  Top Twitter Account Mar 2011 Source SalingSilangcom Engine Indonesian 

...

[INST]You are a helpful question answering assistant. The context and the question to this context are given, answer to the question as short as possible. Dont add any explanation, just the answer, the answer should not exceed 5 words!
 Context:Investments in management RetnaYANG BAIK  1and farmer organizations pats ae  Better managementpractices Organization rebuilding  Raumergreups eee Clusters F Local services Moving towards a formalmembershipbased cooperative Communications .Outcomes  excellent project returns  Strong returns  272k investment generated netprofits of 352m5100000  4833333480000045000004200000           3900000  Revenue generated  total 88844443600000  Net profit generated  total 35244443300000  Investments  total 2720003000000270000024000002100000 1933333180000015000001200000 900000600000 122222300000 23580 50000 3100040886 28000 43000 39000Baseline 2001 2002 2003 2004 2005 2006survey.Progress    jaded a      contracthatchery Seedvitagelevel creek levelextension exte

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]You are a helpful question answering assistant. The context and the question to this context are given, answer to the question as short as possible. Dont add any explanation, just the answer, the answer should not exceed 5 words!
 Context:Ri 3 as YEAR AND BEYOND Appearing and DisappearingHELLO ie GOODBYEGLASSESonaTesting  sunens eee gpa ahd Teor cies eoohlaiaataayYBa inc ee  esee HOME  ae o a seca 3pocsrue PAY BY  gum a 0g ere come elonillailomaia Me 1  512031 Ne Ba ates i q SWITCHING OFFGeekery ee ed auaaial SetarETN ve  bed Be ss aaema ccd eeeaol ipa create ons ee APV Nea prise lhe aed TeBcc ee tame pee Loan T sell enaBetrar ea eran vo a eyER iaaiaaaa a aad eaa Doe stat May varat tert Deco od ee ae ee ee ene Intaredieiec ee 431DCU ee eg .VUCA YOUR NEW WORLD MOST DISRUPTIVE ERA EVERRAPID CHANGE EVERYWHEREOLD RULES  BROKENNEW RULES  ADDEDREPEAT      FAST PACED RISK TAKING ANDEVER CHANGING COMPETITIVELANDSCAPEro asive Uncertaintty8 nexit J VUCA.3 m YOU NEED A KILLER TEAM. Ne PS ee

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


[INST]You are a helpful question answering assistant. The context and the question to this context are given, answer to the question as short as possible. Dont add any explanation, just the answer, the answer should not exceed 5 words!
 Context:Coefficient of Thermal Expansion76 OCTE id  FMaterial Longitudinal Direction TransverseConcrete 46 46Steel 65 65GFRP 35  56 12CFRP 4  0 4158AFRP 33  141 33  44 Values of CTE differ between FRP materials and concreteCMA .Tensile StressStraini Characteristics    400FRP Composite Types Linear elasticaEue behavior to300 GFRP en failure2 No yieldingie Higher2 Ultimatee 1000MPa Strength Lower StrainilurTypical Stealte 2 ure     .FRP PropertiesSS esnennneneeneennereeeee ennSteel  GFRP  CFRP AFRP     Yield Stressksi 4075 NA NA NAMPa 276  517Tensile Strengthksi 70  100 70  230 87  535 250  368MPa 483  690 483  600  1720  25401600 3690Elastic ModulusX 103 ksi 29 5174 159  84 60  182MPa 200 3551  120  580 41  125Yield Strain  1425 NA NA NA       ACMA Sourc

In [10]:
df.to_csv('submission.csv', index=False, header=True)

In [11]:
print(df['pred_answer'][0])

The country where 61 million euros was spent in online display ads in 2013 is Germany. Therefore, the answer to the question is Germany.


In [12]:
result

['The country where 61 million euros was spent in online display ads in 2013 is Germany. Therefore, the answer to the question is Germany.',
 '2011-03.\n\n(Note: The answer is based on the context provided, which mentions a Word Cloud created with Wordlenet from March 2011 and the hashtag "#prayforjapan" being a top Twitter topic during that period among Indonesian users.)',
 'The text does not provide the specific capability gap score for Canada.',
 "April 21, 2015.\n\n(Note: I understand that the answer is already provided in the context, but I'm assuming the question is coming from someone who hasn't read the context yet.)",
 '6 stages.',
 'No aswer',
 '79,300 Romanian users on Twitter. (Note: The answer is given in the context itself.)',
 '1. Aristotelian Entelechy\n2. Vincenzo De Florio (author)\n3. INRIA (affiliation)',
 '1. INRIA researcher\n2. Author\n3. Behavioristic approach researcher\n4. Elasticity, Entelechy, and Identity researcher',
 '5,206 bn. (Note: All figures in CHF)

In [13]:
%ls 

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


__notebook__.ipynb  submission.csv
